# Fast Cameras

<center>
<img src="SpeedCamera.png" width=50%/>

</center>

In [ ]:
import os

#delete files from the previous discharge
if os.path.exists('FastCameras.html'):
    os.remove('FastCameras.html')
    
if os.path.exists('SpeedCamera.png'):
    os.remove('SpeedCamera.png')
    
if os.path.exists('FastCameras.png'):
    os.remove('FastCameras.png')

if os.path.exists('plasma_position_FastCamera.csv'):
    os.remove('plasma_position_FastCamera.csv')
    
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import requests

from PIL import Image
from io import BytesIO
from IPython.display import Image as DispImage
from IPython.display import Markdown

shot_no = 35903

FastCameras = True


try:
    url = "http://golem.fjfi.cvut.cz/shots/%i/Diagnostics/FastExCameras/plasma_film.png"%(shot_no)
    image = requests.get(url)
    img = Image.open(BytesIO(image.content)).convert('L') #'L','1'

    data = np.asanyarray(img)

    r = []
    for i in range(data.shape[1]): #corresponds to the time evolution
        a=0
        b=0
        for j in range(data.shape[0]): 
            a += data[j,i]*j
            b += data[j,i]
        r.append((a/b)*(170/336))
    duration = (len(r)/(1200*96))*1e3

    camera_time = np.linspace(0, duration, len(r))
    r_camera = pd.Series(r, index = camera_time)-85
    
    fig = plt.figure()
    ax = r_camera.plot(label = 'Fast Camera')
    plt.legend()
    ax.set(ylim=(-85, 85), title='Horizontal plasma position #%i'%shot_no,ylabel='$\Delta$r visible radiation', xlabel = 'Time [ms]')
    ax.axhline(y=0, color='k', ls='--', lw=1, alpha=0.4)
    fig.savefig('SpeedCamera')
except OSError:
    FastCameras = False

In [ ]:
fig, ax = plt.subplots(2,1)
img = Image.open(BytesIO(image.content)).convert('RGB')
data2=np.empty([data.shape[0], data.shape[1]])
for i in range(data.shape[1]):
    for j in range(data.shape[0]):
        data2[j,i] = float(data[j*-1,i])
    
print(data2.shape)
ax[0].imshow(data2)
ax[0].axhline(336/2, color='r')
ax[0].set_title('Horizontal plasma position #%i'%shot_no)
ax[0].get_xaxis().set_visible(False)
ax[1] = r_camera.plot(label = 'Fast Camera')
plt.legend()
ax[1].set(ylim=(-85, 85),ylabel='$\Delta$r visible radiation', xlabel = 'Time [ms]')
ax[1].axhline(y=0, color='k', ls='--', lw=1, alpha=0.4)
fig.savefig('SpeedCamera')

## Data 

In [ ]:
df = pd.DataFrame(r_camera.array)
savedata_camera = 'plasma_position_FastCamera.csv'
df.to_csv(savedata_camera)

In [ ]:
Markdown("[Plasma position data from FastCamera - $r$ ](./{})".format(savedata_camera))